# Add working conditions data from EWCS

### Load libraries

In [1]:
import subprocess

import pandas as pd
import pyreadstat

### Load data

In [2]:
df, meta = pyreadstat.read_dta(
    "/Users/alexandralugova/Documents/GitHub/MH-old-workers/data/datasets/EWCS 1991-2015 UKDA ISCO.DTA"
)
variable_labels = meta.column_labels

### Choose only necessary data, tranform where needed

Identify and name the aggregated indexes for work conditions

In [3]:
df = df.rename(
    columns={
        "adincome_mth": "jqi_monthly_earnings",
        "wq": "jqi_skills_discretion",
        # "goodsoc": "jqi_social_environment", - to calculate manually
        "envsec": "jqi_physical_environment",
        # "intens_slim": "jqi_intensity",
        # "prosp": "jqi_prospects", - to calculate manually
        "wlb_slim": "jqi_working_time_quality",
    }
)

Define country names and choose the needed

In [4]:
countid_mapping = meta.value_labels["COUNTID"]
df["countid"] = df["countid"].map(countid_mapping)

In [5]:
countries = [
    "Austria",
    "Belgium",
    "Czech Republic",
    "Denmark",
    "Estonia",
    "France",
    "Germany",
    "Italy",
    "Slovenia",
    "Spain",
    "Switzerland",
]
df = df[df["countid"].isin(countries)].reset_index(drop=True)

Leave only waves 5 and 6 (2010 and 2015)

In [6]:
df = df[df.year >= 2010].reset_index(drop=True)

Drop lines with missing isco codes

In [7]:
df = df.dropna(subset="ISCO_08").reset_index(drop=True)

Adjust some isco codes

In [8]:
def modify_isco(value):
    if len(str(value)) == 1:
        return value * 1000
    elif len(str(value)) == 2:
        return value * 100
    elif len(str(value)) == 3:
        return value * 10
    else:
        return value


df["ISCO_08"] = df["ISCO_08"].apply(modify_isco)

Rename some variables

In [9]:
df = df.rename(columns={"countid": "country", "ISCO_08": "isco"})

Format id column

In [10]:
df["id"] = df["id"].astype(str)
df["id"] = df["id"].str.replace(r"[^ -~]+", "", regex=True)
df["id"] = df["id"].str.strip()

In [11]:
df

id   country  wave  year y15_Q1 y15_Q2a y15_Q2b y15_Q2c  \
0         BE000964   Belgium     6  2015      1       1      40       1   
1         BE000967   Belgium     6  2015      1       2      49       1   
2         BE000968   Belgium     6  2015      2       1      54       1   
3         BE000970   Belgium     6  2015      3       1      52       1   
4         BE000972   Belgium     6  2015      3       1      28       1   
...            ...       ...   ...   ...    ...     ...     ...     ...   
34701  23000011509  Slovenia     5  2010      3       2      63     NaN   
34702  23000011511  Slovenia     5  2010      4       2      21     NaN   
34703  23000011513  Slovenia     5  2010      2       2      48     NaN   
34704  23000011516  Slovenia     5  2010      5       1      41     NaN   
34705  23000011713  Slovenia     5  2010      3       1      43     NaN   

      y15_Q2d y15_Q3a_2  ...     wq_slim    goodsoc jqi_physical_environment  \
0           2       NaN  ...   14.285715  94.444443                66.666664   
1           2       NaN  ...   85.714287        NaN                91.025642   
2           2         2  ...   85.714287        NaN                76.923080   
3           2         2  ...   28.571430  97.916664                98.717949   
4           2         1  ...   42.857143  74.166664                97.435898   
...       ...       ...  ...         ...        ...                      ...   
34701     NaN         1  ...   57.142860        NaN                84.615387   
34702     NaN         1  ...   50.000000        NaN                84.615387   
34703     NaN         1  ...   71.428574        NaN                80.769234   
34704     NaN         1  ...  100.000000        NaN                97.435898   
34705     NaN         2  ...   71.428574        NaN                74.358971   

          intens intens_slim      prosp       wlb jqi_working_time_quality  \
0      31.759258   53.333336  25.000000  69.12500                   88.500   
1      13.148149   24.444445  50.000000  84.50000                   87.500   
2      27.037039   52.222221  50.000000  56.31250                   37.500   
3       9.444445   18.888889  62.500000  86.84375                   96.875   
4      30.833334   53.333336  41.666664  74.28125                   96.875   
...          ...         ...        ...       ...                      ...   
34701        NaN   40.000000        NaN       NaN                  100.000   
34702        NaN   40.000000        NaN       NaN                   62.500   
34703        NaN    6.666667        NaN       NaN                   87.500   
34704        NaN   18.888889        NaN       NaN                   88.500   
34705        NaN   74.444443        NaN       NaN                   46.875   

       isco ISCO_88  
0      8141    8231  
1      5141    5141  
2      1323    1313  
3      7115    7124  
4      8322    8322  
...     ...     ...  
34701  9111    9131  
34702  5131    5123  
34703  5141    5141  
34704  3113    3113  
34705  2434    3415  

[34706 rows x 751 columns]

### Calculate social environment index

Load data for 2010 and 2015

In [12]:
df10, meta10 = pyreadstat.read_dta(
    "/Users/alexandralugova/Documents/GitHub/MH-old-workers/data/datasets/UKDA-2010/stata/stata11/ewcs_2010_version_ukda_6_dec_2011.dta"
)

Calculate the index for 2010

In [13]:
soc10 = df10[
    [
        "id",
        "q70a",
        "q70b",
        "q70c",
        "q71a",
        "q71c",
        "q71b",
        "q58b",
        "q58a",
        "q51a",
        "q51b",
    ]
]
soc10 = soc10.dropna().reset_index(drop=True)
for col in soc10.columns:
    if col != "id":
        soc10[col] = soc10[col].astype("int")
        soc10 = soc10[soc10[col] < 7].reset_index(drop=True)
soc10[["q58a", "q58b"]] = soc10[["q58a", "q58b"]].replace({1: 2, 2: 1})
soc10[["q51a", "q51b"]] = soc10[["q51a", "q51b"]].replace({1: 5, 2: 4, 4: 2, 5: 1})

In [14]:
soc10.describe()

id          q70a          q70b          q70c          q71a  \
count  3.083600e+04  30836.000000  30836.000000  30836.000000  30836.000000   
mean   1.572380e+10      1.891069      1.982196      1.945875      1.980834   
std    1.017743e+10      0.311558      0.132240      0.226268      0.137110   
min    1.000001e+09      1.000000      1.000000      1.000000      1.000000   
25%    6.000005e+09      2.000000      2.000000      2.000000      2.000000   
50%    1.503820e+10      2.000000      2.000000      2.000000      2.000000   
75%    2.500000e+10      2.000000      2.000000      2.000000      2.000000   
max    3.400018e+10      2.000000      2.000000      2.000000      2.000000   

               q71c          q71b          q58b          q58a          q51a  \
count  30836.000000  30836.000000  30836.000000  30836.000000  30836.000000   
mean       1.991017      1.953528      1.950123      1.805682      4.017220   
std        0.094354      0.210508      0.217694      0.395681      1.012743   
min        1.000000      1.000000      1.000000      1.000000      1.000000   
25%        2.000000      2.000000      2.000000      2.000000      3.000000   
50%        2.000000      2.000000      2.000000      2.000000      4.000000   
75%        2.000000      2.000000      2.000000      2.000000      5.000000   
max        2.000000      2.000000      2.000000      2.000000      5.000000   

               q51b  
count  30836.000000  
mean       3.759826  
std        1.164070  
min        1.000000  
25%        3.000000  
50%        4.000000  
75%        5.000000  
max        5.000000

In [15]:
soc10

id  q70a  q70b  q70c  q71a  q71c  q71b  q58b  q58a  q51a  \
0      1.000001e+09     2     2     2     2     2     2     1     2     4   
1      1.000001e+09     2     2     2     2     2     2     2     2     4   
2      1.000001e+09     2     2     2     2     2     2     2     1     4   
3      1.000001e+09     2     2     2     2     2     2     2     1     4   
4      1.000001e+09     2     2     2     2     2     2     2     2     3   
...             ...   ...   ...   ...   ...   ...   ...   ...   ...   ...   
30831  3.400017e+10     2     2     2     2     2     2     2     2     3   
30832  3.400017e+10     2     2     2     2     2     2     2     2     4   
30833  3.400017e+10     2     2     2     2     2     2     2     2     3   
30834  3.400018e+10     2     2     2     2     2     2     2     2     3   
30835  3.400018e+10     2     2     2     2     2     2     2     2     5   

       q51b  
0         1  
1         4  
2         5  
3         3  
4         3  
...     ...  
30831     4  
30832     4  
30833     4  
30834     3  
30835     3  

[30836 rows x 11 columns]

In [16]:
soc10["jqi_social_environment"] = (
    soc10["q58a"]
    + soc10["q58b"]
    + soc10["q51a"]
    + soc10["q51b"]
    + soc10["q70a"]
    + soc10["q70b"]
    + soc10["q70c"]
    + soc10["q71a"]
    + soc10["q71b"]
    + soc10["q71c"]
)

old_min = 10
old_max = 26
new_min = 0
new_max = 100

soc10["jqi_social_environment"] = (
    (soc10["jqi_social_environment"] - old_min) / (old_max - old_min)
) * (new_max - new_min) + new_min

In [17]:
soc10["jqi_social_environment"].describe()

count    30836.000000
mean        82.983566
std         14.530474
min         12.500000
25%         75.000000
50%         87.500000
75%         93.750000
max        100.000000
Name: jqi_social_environment, dtype: float64

In [18]:
soc10 = soc10[["id", "jqi_social_environment"]]
soc10["year"] = 2010

/var/folders/ck/3npmnx597nb730qdy5w_6kp00000gn/T/ipykernel_37458/522855989.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  soc10["year"] = 2010


Calculate the index for 2015

In [19]:
soc15 = df[
    [
        "id",
        "y15_Q80a",
        "y15_Q80b",
        "y15_Q80c",
        "y15_Q81a",
        "y15_Q81b",
        "y15_Q81c",
        "y15_Q63a",
        "y15_Q63e",
        "y15_Q61a",
        "y15_Q61b",
    ]
]
soc15 = soc15.dropna().reset_index(drop=True)
for col in soc15.columns:
    if col != "id":
        soc15[col] = soc15[col].astype("int")
        soc15 = soc15[soc15[col] < 7].reset_index(drop=True)
soc15[["y15_Q61a", "y15_Q61b", "y15_Q63a", "y15_Q63e"]] = soc15[
    ["y15_Q61a", "y15_Q61b", "y15_Q63a", "y15_Q63e"]
].replace({1: 5, 2: 4, 4: 2, 5: 1})

In [20]:
soc15.describe()

y15_Q80a      y15_Q80b      y15_Q80c      y15_Q81a      y15_Q81b  \
count  13279.000000  13279.000000  13279.000000  13279.000000  13279.000000   
mean       1.872430      1.980194      1.950072      1.980420      1.990737   
std        0.333623      0.139337      0.217805      0.138556      0.095800   
min        1.000000      1.000000      1.000000      1.000000      1.000000   
25%        2.000000      2.000000      2.000000      2.000000      2.000000   
50%        2.000000      2.000000      2.000000      2.000000      2.000000   
75%        2.000000      2.000000      2.000000      2.000000      2.000000   
max        2.000000      2.000000      2.000000      2.000000      2.000000   

           y15_Q81c      y15_Q63a      y15_Q63e      y15_Q61a      y15_Q61b  
count  13279.000000  13279.000000  13279.000000  13279.000000  13279.000000  
mean       1.941637      4.426538      3.817682      3.967543      3.644100  
std        0.234437      0.855332      1.163330      1.079077      1.223853  
min        1.000000      1.000000      1.000000      1.000000      1.000000  
25%        2.000000      4.000000      3.000000      3.000000      3.000000  
50%        2.000000      5.000000      4.000000      4.000000      4.000000  
75%        2.000000      5.000000      5.000000      5.000000      5.000000  
max        2.000000      5.000000      5.000000      5.000000      5.000000

In [21]:
soc15["jqi_social_environment"] = (
    soc15["y15_Q80a"]
    + soc15["y15_Q80b"]
    + soc15["y15_Q80c"]
    + soc15["y15_Q81a"]
    + soc15["y15_Q81b"]
    + soc15["y15_Q81c"]
    + soc15["y15_Q63a"]
    + soc15["y15_Q63e"]
    + soc15["y15_Q61a"]
    + soc15["y15_Q61b"]
)

old_min = 10
old_max = 32
new_min = 0
new_max = 100

soc15["jqi_social_environment"] = (
    (soc15["jqi_social_environment"] - old_min) / (old_max - old_min)
) * (new_max - new_min) + new_min

In [22]:
soc15["jqi_social_environment"].describe()

count    13279.000000
mean        79.869788
std         15.768143
min          9.090909
25%         72.727273
50%         81.818182
75%         90.909091
max        100.000000
Name: jqi_social_environment, dtype: float64

In [23]:
soc15 = soc15[["id", "jqi_social_environment"]]
soc15["year"] = 2015

Add indexes to main df

In [24]:
soc = pd.concat([soc10, soc15], axis=0).reset_index(drop=True)

In [25]:
soc["id"] = soc["id"].astype(str)
soc["id"] = soc["id"].astype(str).apply(lambda x: x[:-2] if x.endswith(".0") else x)
soc["id"] = soc["id"].str.replace(r"[^ -~]+", "", regex=True)

In [26]:
df = df.merge(soc, on=["id", "year"], how="left")

In [27]:
unique_mergeid_df = set(df["id"].unique())
unique_mergeid_soc = set(soc["id"].unique())
intersection_ids = unique_mergeid_df.intersection(unique_mergeid_soc)
len(intersection_ids)

25750

### Calculate prospects index

Index for 2010

In [28]:
pro10 = df10[["id", "q77c", "q77a"]]
pro10 = pro10.dropna().reset_index(drop=True)
for col in pro10.columns:
    if col != "id":
        pro10[col] = pro10[col].astype("int")
        pro10 = pro10[pro10[col] < 7].reset_index(drop=True)
pro10["q77a"] = pro10["q77a"].replace({1: 5, 2: 4, 4: 2, 5: 1})

In [29]:
pro10.describe()

id          q77c          q77a
count  3.855600e+04  38556.000000  38556.000000
mean   1.610812e+10      2.745746      3.706660
std    1.032083e+10      1.199690      1.226394
min    1.000001e+09      1.000000      1.000000
25%    7.000102e+09      2.000000      3.000000
50%    1.538090e+10      3.000000      4.000000
75%    2.600020e+10      4.000000      5.000000
max    3.400018e+10      5.000000      5.000000

In [30]:
pro10["jqi_prospects"] = pro10["q77c"] + pro10["q77a"]

old_min = 2
old_max = 10
new_min = 0
new_max = 100

pro10["jqi_prospects"] = ((pro10["jqi_prospects"] - old_min) / (old_max - old_min)) * (
    new_max - new_min
) + new_min

In [31]:
pro10["jqi_prospects"].describe()

count    38556.000000
mean        55.655086
std         23.024819
min          0.000000
25%         37.500000
50%         50.000000
75%         75.000000
max        100.000000
Name: jqi_prospects, dtype: float64

In [32]:
pro10 = pro10[["id", "jqi_prospects"]]
pro10["year"] = 2010

Index for 2015

In [33]:
pro15 = df[["id", "y15_Q89b", "y15_Q89g"]]
pro15 = pro15.dropna().reset_index(drop=True)
for col in pro15.columns:
    if col != "id":
        pro15[col] = pro15[col].astype("int")
        pro15 = pro15[pro15[col] < 7].reset_index(drop=True)
pro15["y15_Q89b"] = pro15["y15_Q89b"].replace({1: 5, 2: 4, 4: 2, 5: 1})

In [34]:
pro15.describe()

y15_Q89b      y15_Q89g
count  30073.000000  30073.000000
mean       2.797626      3.840555
std        1.282885      1.270620
min        1.000000      1.000000
25%        2.000000      3.000000
50%        3.000000      4.000000
75%        4.000000      5.000000
max        5.000000      5.000000

In [35]:
pro15["jqi_prospects"] = pro15["y15_Q89g"] + pro15["y15_Q89b"]

old_min = 2
old_max = 10
new_min = 0
new_max = 100

pro15["jqi_prospects"] = ((pro15["jqi_prospects"] - old_min) / (old_max - old_min)) * (
    new_max - new_min
) + new_min

In [36]:
pro15["jqi_prospects"].describe()

count    30073.000000
mean        57.977255
std         24.018895
min          0.000000
25%         50.000000
50%         62.500000
75%         75.000000
max        100.000000
Name: jqi_prospects, dtype: float64

In [37]:
pro15 = pro15[["id", "jqi_prospects"]]
pro15["year"] = 2015

Add indexes to main df

In [38]:
pro = pd.concat([pro10, pro15], axis=0).reset_index(drop=True)

In [39]:
pro["id"] = pro["id"].astype(str)
pro["id"] = pro["id"].astype(str).apply(lambda x: x[:-2] if x.endswith(".0") else x)
pro["id"] = pro["id"].str.replace(r"[^ -~]+", "", regex=True)

In [40]:
df = df.merge(pro, on=["id", "year"], how="left")

In [41]:
unique_mergeid_df = set(df["id"].unique())
unique_mergeid_pro = set(pro["id"].unique())
intersection_ids = unique_mergeid_df.intersection(unique_mergeid_pro)
len(intersection_ids)

30073

### Calculate intensity index

Index for 2010

In [42]:
int10 = df10[
    [
        "id",
        "q45a",
        "q45b",
        "q51g",
        "q46a",
        "q46b",
        "q46c",
        "q46d",
        "q46e",
        "q51p",
        "q24g",
        "q47",
        "q48",
    ]
]
int10 = int10.dropna().reset_index(drop=True)
for col in int10.columns:
    if col != "id" and col != "q46e":
        int10[col] = int10[col].astype("int")
        int10 = int10[int10[col] < 8].reset_index(drop=True)
    elif col == "q46e":
        int10[col] = int10[col].astype("int")
        int10 = int10[int10[col] < 7].reset_index(drop=True)

int10["q4748"] = int10["q47"] * int10["q48"]

int10["q46"] = 2
for i in range(len(int10)):
    count = 0
    for col in ["q46a", "q46b", "q46c", "q46d", "q46e"]:
        if int10[col][i] == 1:
            count += 1
    if count >= 3:
        int10["q46"][i] = 1

int10["q51g"] = int10["q51g"].replace({1: 5, 2: 4, 4: 2, 5: 1})

/var/folders/ck/3npmnx597nb730qdy5w_6kp00000gn/T/ipykernel_37458/3831146219.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  int10["q46"][i] = 1
/var/folders/ck/3npmnx597nb730qdy5w_6kp00000gn/T/ipykernel_37458/3831146219.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  int10["q46"][i] = 1
/var/folders/ck/3npmnx597nb730qdy5w_6kp00000gn/T/ipykernel_37458/3831146219.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  int10["q46"]

In [43]:
int10.describe()

id          q45a          q45b          q51g          q46a  \
count  2.706300e+04  27063.000000  27063.000000  27063.000000  27063.000000   
mean   1.556218e+10      4.323061      4.219857      3.915235      1.518826   
std    1.009079e+10      1.981461      2.030365      0.997920      0.499655   
min    1.000001e+09      1.000000      1.000000      1.000000      1.000000   
25%    7.000022e+09      2.000000      2.000000      3.000000      1.000000   
50%    1.503811e+10      5.000000      4.000000      4.000000      2.000000   
75%    2.400016e+10      6.000000      6.000000      5.000000      2.000000   
max    3.400017e+10      7.000000      7.000000      5.000000      2.000000   

               q46b          q46c          q46d          q46e          q51p  \
count  27063.000000  27063.000000  27063.000000  27063.000000  27063.000000   
mean       1.304327      1.623841      1.818128      1.590548      3.319772   
std        0.460130      0.484430      0.385746      0.491742      1.389524   
min        1.000000      1.000000      1.000000      1.000000      1.000000   
25%        1.000000      1.000000      2.000000      1.000000      2.000000   
50%        1.000000      2.000000      2.000000      2.000000      3.000000   
75%        2.000000      2.000000      2.000000      2.000000      5.000000   
max        2.000000      2.000000      2.000000      2.000000      5.000000   

               q24g           q47           q48         q4748           q46  
count  27063.000000  27063.000000  27063.000000  27063.000000  27063.000000  
mean       5.629827      2.429295      1.746296      4.343790      1.624986  
std        1.606418      0.756038      0.597895      2.115829      0.484135  
min        1.000000      1.000000      1.000000      1.000000      1.000000  
25%        5.000000      2.000000      1.000000      2.000000      1.000000  
50%        6.000000      3.000000      2.000000      4.000000      2.000000  
75%        7.000000      3.000000      2.000000      6.000000      2.000000  
max        7.000000      3.000000      3.000000      9.000000      2.000000

In [44]:
int10["jqi_intensity"] = (
    int10["q45a"]
    + int10["q45b"]
    + int10["q51g"]
    + int10["q46a"]
    + int10["q46b"]
    + int10["q46c"]
    + int10["q46d"]
    + int10["q46e"]
    + int10["q46"]
    + int10["q51p"]
    + int10["q24g"]
    + int10["q4748"]
)

old_min = 11
old_max = 54
new_min = 0
new_max = 100

int10["jqi_intensity"] = ((int10["jqi_intensity"] - old_min) / (old_max - old_min)) * (
    new_max - new_min
) + new_min

In [45]:
int10["jqi_intensity"].describe()

count    27063.000000
mean        56.353951
std         15.846348
min          4.651163
25%         46.511628
50%         58.139535
75%         67.441860
max         95.348837
Name: jqi_intensity, dtype: float64

In [46]:
int10 = int10[["id", "jqi_intensity"]]
int10["year"] = 2010

Index for 2015

In [47]:
int15 = df[
    [
        "id",
        "y15_Q49a",
        "y15_Q49b",
        "y15_Q61g",
        "y15_Q50a",
        "y15_Q50b",
        "y15_Q50c",
        "y15_Q50d",
        "y15_Q50e",
        "y15_Q61o",
        "y15_Q30g",
        "y15_Q51",
        "y15_Q52",
    ]
]
int15 = int15.dropna().reset_index(drop=True)
for col in int15.columns:
    if col != "id":
        int15[col] = int15[col].astype("int")
        int15 = int15[int15[col] < 7].reset_index(drop=True)

int15["y15_Q5152"] = int15["y15_Q51"] * int15["y15_Q52"]

int15["y15_Q50"] = 0
for i in range(len(int15)):
    count = 0
    for col in ["y15_Q50a", "y15_Q50b", "y15_Q50c", "y15_Q50d", "y15_Q50e"]:
        if int15[col][i] == 1:
            count += 1
    if count >= 3:
        int15["y15_Q50"][i] = 1

int15["y15_Q61g"] = int15["y15_Q61g"].replace({1: 5, 2: 4, 4: 2, 5: 1})

/var/folders/ck/3npmnx597nb730qdy5w_6kp00000gn/T/ipykernel_37458/1060183057.py:33: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  int15["y15_Q50"][i] = 1
/var/folders/ck/3npmnx597nb730qdy5w_6kp00000gn/T/ipykernel_37458/1060183057.py:33: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  int15["y15_Q50"][i] = 1
/var/folders/ck/3npmnx597nb730qdy5w_6kp00000gn/T/ipykernel_37458/1060183057.py:33: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  int1

In [48]:
int15.describe()

y15_Q49a      y15_Q49b      y15_Q61g      y15_Q50a      y15_Q50b  \
count  12947.000000  12947.000000  12947.000000  12947.000000  12947.000000   
mean       3.700935      3.607786      3.692979      1.526377      1.173322   
std        1.682326      1.737535      0.979734      0.499323      0.378540   
min        1.000000      1.000000      1.000000      1.000000      1.000000   
25%        2.000000      2.000000      3.000000      1.000000      1.000000   
50%        4.000000      4.000000      4.000000      2.000000      1.000000   
75%        5.000000      5.000000      4.000000      2.000000      1.000000   
max        6.000000      6.000000      5.000000      2.000000      2.000000   

           y15_Q50c      y15_Q50d      y15_Q50e      y15_Q61o      y15_Q30g  \
count  12947.000000  12947.000000  12947.000000  12947.000000  12947.000000   
mean       1.566386      1.837260      1.627018      3.125975      4.735923   
std        0.495592      0.369143      0.483616      1.341201      1.604203   
min        1.000000      1.000000      1.000000      1.000000      1.000000   
25%        1.000000      2.000000      1.000000      2.000000      4.000000   
50%        2.000000      2.000000      2.000000      3.000000      5.000000   
75%        2.000000      2.000000      2.000000      4.000000      6.000000   
max        2.000000      2.000000      2.000000      5.000000      6.000000   

            y15_Q51       y15_Q52     y15_Q5152       y15_Q50  
count  12947.000000  12947.000000  12947.000000  12947.000000  
mean       2.350583      1.614737      3.899900      0.404264  
std        0.764868      0.591948      2.044807      0.490768  
min        1.000000      1.000000      1.000000      0.000000  
25%        2.000000      1.000000      2.000000      0.000000  
50%        3.000000      2.000000      3.000000      0.000000  
75%        3.000000      2.000000      6.000000      1.000000  
max        3.000000      3.000000      9.000000      1.000000

In [49]:
int15["jqi_intensity"] = (
    int15["y15_Q49a"]
    + int15["y15_Q49b"]
    + int15["y15_Q61g"]
    + int15["y15_Q50a"]
    + int15["y15_Q50b"]
    + int15["y15_Q50c"]
    + int15["y15_Q50d"]
    + int15["y15_Q50e"]
    + int15["y15_Q50"]
    + int15["y15_Q61o"]
    + int15["y15_Q30g"]
    + int15["y15_Q5152"]
)

old_min = 11
old_max = 54
new_min = 0
new_max = 100

int15["jqi_intensity"] = ((int15["jqi_intensity"] - old_min) / (old_max - old_min)) * (
    new_max - new_min
) + new_min

In [50]:
int15["jqi_intensity"].describe()

count    12947.000000
mean        46.274705
std         13.852596
min          2.325581
25%         37.209302
50%         46.511628
75%         55.813953
max         83.720930
Name: jqi_intensity, dtype: float64

In [51]:
int15 = int15[["id", "jqi_intensity"]]
int15["year"] = 2015

Add indexes to main df

In [52]:
int = pd.concat([int10, int15], axis=0).reset_index(drop=True)

In [53]:
int["id"] = int["id"].astype(str)
int["id"] = int["id"].astype(str).apply(lambda x: x[:-2] if x.endswith(".0") else x)
int["id"] = int["id"].str.replace(r"[^ -~]+", "", regex=True)

In [54]:
df = df.merge(int, on=["id", "year"], how="left")

In [55]:
unique_mergeid_df = set(df["id"].unique())
unique_mergeid_int = set(int["id"].unique())
intersection_ids = unique_mergeid_df.intersection(unique_mergeid_int)
len(intersection_ids)

18419

### Add country level post-stratification weights

In [56]:
columns_to_multiply = [
    "jqi_monthly_earnings",
    "jqi_skills_discretion",
    "jqi_social_environment",
    "jqi_physical_environment",
    "jqi_intensity",
    "jqi_prospects",
    "jqi_working_time_quality",
]

for column in columns_to_multiply:
    df[f"{column}_weighted"] = df[column] * df["w4"]

### Add sum of indexes

Normal

In [57]:
df["jqi_sum"] = (
    +df["jqi_skills_discretion"]
    + df["jqi_social_environment"]
    + df["jqi_physical_environment"]
    + df["jqi_intensity"]
    + df["jqi_prospects"]
    + df["jqi_working_time_quality"]
)

In [58]:
df["jqi_sum"].describe()

count    13926.000000
mean       419.805953
std         59.874116
min        133.185597
25%        383.844714
50%        425.971467
75%        463.307343
max        575.941286
Name: jqi_sum, dtype: float64

Weighted

In [59]:
df["jqi_sum_weighted"] = (
    +df["jqi_skills_discretion_weighted"]
    + df["jqi_social_environment_weighted"]
    + df["jqi_physical_environment_weighted"]
    + df["jqi_intensity_weighted"]
    + df["jqi_prospects_weighted"]
    + df["jqi_working_time_quality_weighted"]
)

In [60]:
df["jqi_sum_weighted"].describe()

count    13926.000000
mean       431.165504
std        253.552717
min         40.274174
25%        246.390676
50%        368.014244
75%        544.066005
max       2656.738863
Name: jqi_sum_weighted, dtype: float64

In [61]:
df

id   country  wave  year y15_Q1 y15_Q2a y15_Q2b y15_Q2c  \
0         BE000964   Belgium     6  2015      1       1      40       1   
1         BE000967   Belgium     6  2015      1       2      49       1   
2         BE000968   Belgium     6  2015      2       1      54       1   
3         BE000970   Belgium     6  2015      3       1      52       1   
4         BE000972   Belgium     6  2015      3       1      28       1   
...            ...       ...   ...   ...    ...     ...     ...     ...   
34701  23000011509  Slovenia     5  2010      3       2      63     NaN   
34702  23000011511  Slovenia     5  2010      4       2      21     NaN   
34703  23000011513  Slovenia     5  2010      2       2      48     NaN   
34704  23000011516  Slovenia     5  2010      5       1      41     NaN   
34705  23000011713  Slovenia     5  2010      3       1      43     NaN   

      y15_Q2d y15_Q3a_2  ... jqi_intensity jqi_monthly_earnings_weighted  \
0           2       NaN  ...           NaN                    903.657300   
1           2       NaN  ...           NaN                           NaN   
2           2         2  ...     60.465116                    770.161311   
3           2         2  ...           NaN                    943.044961   
4           2         1  ...           NaN                    754.819666   
...       ...       ...  ...           ...                           ...   
34701     NaN         1  ...           NaN                    113.467863   
34702     NaN         1  ...     65.116279                    530.970737   
34703     NaN         1  ...           NaN                    165.145245   
34704     NaN         1  ...     79.069767                   1065.008474   
34705     NaN         2  ...     34.883721                   1754.351442   

      jqi_skills_discretion_weighted jqi_social_environment_weighted  \
0                           5.041595                       56.372266   
1                          20.449089                             NaN   
2                          32.674170                             NaN   
3                          25.644061                       59.869880   
4                          18.183448                       42.950298   
...                              ...                             ...   
34701                      47.278745                             NaN   
34702                      41.498448                       69.072833   
34703                      22.903454                             NaN   
34704                     127.447402                      142.097075   
34705                      88.509903                      102.406313   

      jqi_physical_environment_weighted  jqi_intensity_weighted  \
0                             39.371105                     NaN   
1                             28.806330                     NaN   
2                             32.909586               25.868464   
3                             59.102318                     NaN   
4                             57.542387                     NaN   
...                                 ...                     ...   
34701                         96.076142                     NaN   
34702                         71.933840               55.357119   
34703                         30.508954                     NaN   
34704                        138.453561              112.355827   
34705                         87.026606               40.826437   

      jqi_prospects_weighted jqi_working_time_quality_weighted     jqi_sum  \
0                   0.000000                         52.265144         NaN   
1                        NaN                         27.690591         NaN   
2                        NaN                         16.043422         NaN   
3                  44.902410                         57.998946         NaN   
4                  22.146248                         57.211139         NaN   
...                      ...                               ...  

### Aggregate on the level of isco, year and country

In [63]:
# Choose columns
df1 = df[
    [
        "country",
        "year",
        "isco",
        "jqi_monthly_earnings",
        "jqi_skills_discretion",
        "jqi_social_environment",
        "jqi_physical_environment",
        "jqi_intensity",
        "jqi_prospects",
        "jqi_working_time_quality",
        "jqi_monthly_earnings_weighted",
        "jqi_skills_discretion_weighted",
        "jqi_social_environment_weighted",
        "jqi_physical_environment_weighted",
        "jqi_intensity_weighted",
        "jqi_prospects_weighted",
        "jqi_working_time_quality_weighted",
        "jqi_sum",
        "jqi_sum_weighted",
    ]
]

In [64]:
df1 = df1.groupby(["country", "year", "isco"]).mean().reset_index(drop=False)

In [65]:
df1 = df1.dropna().reset_index(drop=True)

Interpolate to obtain approximation of values for 2013

In [66]:
df1["year"] = pd.to_datetime(df1["year"], format="%Y")

df_2010 = df1[df1["year"].dt.year == 2010]
df_2015 = df1[df1["year"].dt.year == 2015]

df_2013 = pd.DataFrame()

for country in df1["country"].unique():
    for isco in df1["isco"].unique():
        data_2010 = df_2010[(df_2010["country"] == country) & (df_2010["isco"] == isco)]
        data_2015 = df_2015[(df_2015["country"] == country) & (df_2015["isco"] == isco)]

        if not data_2010.empty and not data_2015.empty:
            interpolated_values_2013 = data_2010.iloc[0, 3:].interpolate(
                method="linear", limit_area="inside", limit=1
            ) + (data_2015.iloc[0, 3:] - data_2010.iloc[0, 3:]).multiply(3 / 5)

            interpolated_values_2013.index = data_2010.columns[3:]

            row_2013 = pd.DataFrame(
                {
                    "country": [country],
                    "year": [pd.Timestamp(year=2013, month=1, day=1)],
                    "isco": [isco],
                }
            ).join(interpolated_values_2013.to_frame().T.reset_index(drop=True))

            df_2013 = pd.concat([df_2013, row_2013], ignore_index=True)

df1 = pd.concat([df1, df_2013], ignore_index=True)
df1["year"] = pd.to_datetime(df1["year"], format="%Y")
df1["year"] = df1["year"].dt.year

/var/folders/ck/3npmnx597nb730qdy5w_6kp00000gn/T/ipykernel_37458/3450736267.py:14: FutureWarning: Series.interpolate with object dtype is deprecated and will raise in a future version. Call obj.infer_objects(copy=False) before interpolating instead.
  interpolated_values_2013 = data_2010.iloc[0, 3:].interpolate(
/var/folders/ck/3npmnx597nb730qdy5w_6kp00000gn/T/ipykernel_37458/3450736267.py:14: FutureWarning: Series.interpolate with object dtype is deprecated and will raise in a future version. Call obj.infer_objects(copy=False) before interpolating instead.
  interpolated_values_2013 = data_2010.iloc[0, 3:].interpolate(
/var/folders/ck/3npmnx597nb730qdy5w_6kp00000gn/T/ipykernel_37458/3450736267.py:14: FutureWarning: Series.interpolate with object dtype is deprecated and will raise in a future version. Call obj.infer_objects(copy=False) before interpolating instead.
  interpolated_values_2013 = data_2010.iloc[0, 3:].interpolate(
/var/folders/ck/3npmnx597nb730qdy5w_6kp00000gn/T/ipykernel

In [67]:
df1["year"] = df1["year"].replace({2010: 2011})

In [68]:
df1

country  year  isco jqi_monthly_earnings jqi_skills_discretion  \
0     Austria  2011  1114          2366.148112             77.290234   
1     Austria  2011  1120          3143.596761             83.616787   
2     Austria  2011  1219          1588.023401              64.30635   
3     Austria  2011  1321          2788.674561             66.906092   
4     Austria  2011  1324          1799.962646             65.660399   
...       ...   ...   ...                  ...                   ...   
4268    Spain  2013  9334          1046.085136             39.659487   
4269    Spain  2013  2100          2069.535937             66.338245   
4270    Spain  2013  3258          1435.902368             67.310957   
4271    Spain  2013  4212          1261.978491             50.317439   
4272    Spain  2013  7533           617.640436               43.9013   

     jqi_social_environment jqi_physical_environment jqi_intensity  \
0                     100.0                97.863248     52.325581   
1                      87.5                85.042736     53.820598   
2                     93.75                89.903848     65.697674   
3                     81.25                72.863248     45.348837   
4                      87.5                87.948718          50.0   
...                     ...                      ...           ...   
4268              84.363636                81.911422     46.678593   
4269                   97.5                 88.46154     59.069767   
4270              96.363636                 71.28205      52.55814   
4271              93.522727                78.076923     41.860465   
4272              90.227273                82.365386     59.534884   

     jqi_prospects jqi_working_time_quality jqi_monthly_earnings_weighted  \
0             75.0                    100.0                   3034.577207   
1        78.571429                   53.125                   1638.952541   
2           59.375                 85.15625                   1166.245217   
3             75.0                  60.0625                   2632.194486   
4             62.5                    83.75                   1804.782956   
...            ...                      ...                           ...   
4268     46.985294                82.545455                   1092.568983   
4269          57.5                    98.75                   3654.135875   
4270          57.5                     68.7                   1456.858411   
4271          67.5                  75.3875                    782.891747   
4272         36.25                83.921875                    440.003997   

     jqi_skills_discretion_weighted jqi_social_environment_weighted  \
0                          94.40666                        60.31181   
1                         52.464895                       47.019517   
2                         44.854093                       82.620009   
3                         96.736029                       97.872116   
4                         67.982449                       43.819472   
...                             ...                             ...   
4268                      43.613822                       88.254037   
4269                     115.455341                      170.467285   
4270                      72.508648                      100.578868   
4271                      38.370388                       74.793264   
4272                      45.112082                       66.129333   

     jqi_physical_environment_weighted jqi_intensity_weighted  \
0                           121.392346              47.096205   
1                            53.989173                34.3123   
2                            60.938954              54.299599   
3                           105.282028               57.58021   
4                            94.822467              52.969386   
...                                ...                    ...   
4268                         84.228471              38.838715   
42

In [68]:
df1.to_csv(
    "/Users/alexandralugova/Documents/GitHub/MH-old-workers/data/datasets/results/work_quality_indexes_year_country.csv",
    index=False,
)

### Aggregate on the level of isco and year 

In [69]:
# Choose columns
df2 = df[
    [
        "year",
        "isco",
        "jqi_monthly_earnings",
        "jqi_skills_discretion",
        "jqi_social_environment",
        "jqi_physical_environment",
        "jqi_intensity",
        "jqi_prospects",
        "jqi_working_time_quality",
        "jqi_monthly_earnings_weighted",
        "jqi_skills_discretion_weighted",
        "jqi_social_environment_weighted",
        "jqi_physical_environment_weighted",
        "jqi_intensity_weighted",
        "jqi_prospects_weighted",
        "jqi_working_time_quality_weighted",
        "jqi_sum",
        "jqi_sum_weighted",
    ]
]

In [70]:
df2 = df2.groupby(["year", "isco"]).mean().reset_index(drop=False)

In [71]:
df2 = df2.dropna().reset_index(drop=True)

Interpolate to obtain approximation of values for 2013

In [72]:
df2["year"] = pd.to_datetime(df2["year"], format="%Y")

df_2010 = df2[df2["year"].dt.year == 2010]
df_2015 = df2[df2["year"].dt.year == 2015]

df_2013 = pd.DataFrame()

for isco in df2["isco"].unique():
    data_2010 = df_2010[df_2010["isco"] == isco]
    data_2015 = df_2015[df_2015["isco"] == isco]

    if not data_2010.empty and not data_2015.empty:
        interpolated_values_2013 = data_2010.iloc[0, 2:].interpolate(
            method="linear", limit_area="inside", limit=1
        ) + (data_2015.iloc[0, 2:] - data_2010.iloc[0, 2:]).multiply(3 / 5)

        interpolated_values_2013.index = data_2010.columns[2:]

        row_2013 = pd.DataFrame(
            {
                "year": [pd.Timestamp(year=2013, month=1, day=1)],
                "isco": [isco],
            }
        ).join(interpolated_values_2013.to_frame().T.reset_index(drop=True))

        df_2013 = pd.concat([df_2013, row_2013], ignore_index=True)

df2 = pd.concat([df2, df_2013], ignore_index=True)
df2["year"] = pd.to_datetime(df2["year"], format="%Y")
df2["year"] = df2["year"].dt.year

/var/folders/ck/3npmnx597nb730qdy5w_6kp00000gn/T/ipykernel_29530/1358880233.py:13: FutureWarning: Series.interpolate with object dtype is deprecated and will raise in a future version. Call obj.infer_objects(copy=False) before interpolating instead.
  interpolated_values_2013 = data_2010.iloc[0, 2:].interpolate(
/var/folders/ck/3npmnx597nb730qdy5w_6kp00000gn/T/ipykernel_29530/1358880233.py:13: FutureWarning: Series.interpolate with object dtype is deprecated and will raise in a future version. Call obj.infer_objects(copy=False) before interpolating instead.
  interpolated_values_2013 = data_2010.iloc[0, 2:].interpolate(
/var/folders/ck/3npmnx597nb730qdy5w_6kp00000gn/T/ipykernel_29530/1358880233.py:13: FutureWarning: Series.interpolate with object dtype is deprecated and will raise in a future version. Call obj.infer_objects(copy=False) before interpolating instead.
  interpolated_values_2013 = data_2010.iloc[0, 2:].interpolate(
/var/folders/ck/3npmnx597nb730qdy5w_6kp00000gn/T/ipykernel

In [73]:
df2["year"] = df2["year"].replace({2010: 2011})

In [74]:
df2

year  isco jqi_monthly_earnings jqi_skills_discretion  \
0     2011  1100          2587.962799             69.381842   
1     2011  1111          2250.212012             72.508442   
2     2011  1112          2321.469202             70.534725   
3     2011  1114          1989.939789             77.824947   
4     2011  1120          2457.219682             80.784538   
...    ...   ...                  ...                   ...   
1111  2013  9613           890.461025             32.916559   
1112  2013  9621          1035.468639             36.916921   
1113  2013  9622          1013.696387             42.122602   
1114  2013  9623          1876.918372             56.138174   
1115  2013  9629           961.947337             39.038254   

     jqi_social_environment jqi_physical_environment jqi_intensity  \
0                    90.625                90.909092     57.293869   
1                 85.714286                91.025642      60.13289   
2                 79.583333                89.136303     47.227191   
3                     93.75                94.172495     57.364341   
4                      85.0                90.104732      54.99031   
...                     ...                      ...           ...   
1111              74.325069                72.912467     58.161683   
1112               74.17445                82.967113      43.70801   
1113              76.221834                76.978023     60.099668   
1114              84.431818                77.564103     48.372093   
1115              73.289177                85.786326     58.737542   

     jqi_prospects jqi_working_time_quality jqi_monthly_earnings_weighted  \
0             75.0                98.011364                   2384.988548   
1          70.3125                     85.0                   2453.299933   
2        63.888889                81.190789                   2426.633879   
3        56.944444                85.227273                   2275.227127   
4            66.25                65.137911                   3704.684725   
...            ...                      ...                           ...   
1111     45.826923                91.558011                    705.429415   
1112     50.690586                83.485441                    867.695985   
1113     47.272727                96.189286                    985.445679   
1114          55.0                   73.525                   1841.243587   
1115     49.492308                84.995278                    848.638969   

     jqi_skills_discretion_weighted jqi_social_environment_weighted  \
0                         63.621495                       85.602383   
1                         70.387276                       71.683611   
2                         69.585232                       89.177723   
3                         88.627626                      102.627818   
4                        139.517336                       129.35272   
...                             ...                             ...   
1111                      27.113838                       62.298783   
1112                      31.468296                       62.659457   
1113                      37.204711                       66.438476   
1114                      54.120743                       51.463504   
1115                      35.154774                       70.569917   

     jqi_physical_environment_weighted jqi_intensity_weighted  \
0                            83.055189              51.259031   
1                            90.203566              70.144032   
2                            85.956303              49.152847   
3                           108.335033              55.329127   
4                           153.578265              88.700373   
...                                ...                    ...   
1111                          59.24481              51.368231   
1112                         72.162075               35.36361   
1113                         67.253493       

In [75]:
df2.to_csv(
    "/Users/alexandralugova/Documents/GitHub/MH-old-workers/data/datasets/results/work_quality_indexes_year.csv",
    index=False,
)